What is to be done:

GP properties:
* dim
* ambient dim
* n_vertices, n_facets, ...
* is equivalent up to symmetries
* Normal fan (= merging of braid fan)

GP constructors:
* graphical zonotope
* nestohedron, graph associahedron
* hypergraphic polytope
* matroid polytope
* removahedron
* brick polytope
* positroid
* cut function
* 

GP implementations:
1. $\sum_{X\subseteq[n]} y_X \Delta_X$
2. $\sum_{\alpha} s_{\alpha} S_{\alpha}$
3. submodular function
4. Sage polytope
5. edge lengths (awfull) ?

Crypto-morphisms

1. $\sum_{X\subseteq[n]} y_X \Delta_X$
2. $\sum_{\alpha} s_{\alpha} S_{\alpha}$
3. submodular function
4. Sage polytope
6. edge lengths (awfull) ?

$\square$ 1 -> 2 : Sparse Matrix mult of size $2^n \times 2^n$ (see Vincent's paper)

$\square$ 2 -> 1 : Sparse Matrix mult of size $2^n \times 2^n$ (see Vincent's paper)

1 -> 3 : add submodular func of simplices

2 -> 3 : add submodular func of shard polytopes

$\square$ 3 -> 1 : solve (right) matrix $2^n \times 2^n$ on vector length $2^n$ (but matrix construction badly optimized)

$\square$ 3 -> 2 : solve (right) matrix $2^n \times 2^n$ on vector length $2^n$ (but matrix construction badly optimized)

4 -> 1 : ...

4 -> 2 : ...

$\square$ 4 -> 3 : maximize $e_X$ on $V(P)$ for all $X$, i.e. $2^n\times |V(P)|$ complexity (to be optimized)

$\square$ 1 -> 4 : Sage Minkowski sum

$\square$ 2 -> 4 : Sage Minkowski sum

$\square$ 3 -> 4 : Sage Polyhedron (Fourier-Motzkin)

---

On Normal fan merging:

4 -> 5 : maximize all permutations on $V(P)$, i.e. $n! \times |V(P)|$ complexity (to be optimized)

5 -> 4 : Compute DC and realize ? Heuristics : find all X such that fan coarsens normal_fan(Delta_X), and check ? idem shards ? 

1 -> 5 : common refinement of mergings

2 -> 5 : common refinement of mergings

3 -> 5 : ...

In [34]:
class GeneralizedPermutahedra():
    """A class to deal with genralized permutahedra.
    NB:
    polytope: shall be given in R^n in hyperplane sum_i x_i = constant
    submodular_function, shards_vector, simplices_vector: a dict with keys are Subsets(range(n)) (except empty-set)
    submodular_function: embedd the polytope in sum_i x_i = sub_mod[range(n)]
    braid_merging: a list of lists of permutations
    edge_length_vector: no implemented yet
    """
    def __init__(self, data, dtype="polytope"):
        self.n = None
        
        self.polytope = None
        self.submodular_func = None
        self.shards_vector = None
        self.simplices_vector = None
        self.is_sparse_simplicies_vector = False
        self.is_sparse_shards_vector = False
        self.simplicies_used = set()
        self.shards_used = set()
        self.edge_length_vector = None
        
        self.braid_merging = None
        
        if "olytop" in dtype:
            self.polytope = data
            self.n = data.ambient_dim
        elif "odular" in dtype:
            self.submodular_func = data
            self.n = max(len(data.keys()))
        elif "fan" in dtype or "merg" in dtype:
            self.braid_merging = data
            self.n = len(data[0])
        elif "hard" in dtype:
            self.shard_vector = vector(data)
            self.n = int(log(len(data), 2))
        elif "impl" in dtype:
            self.simplicies_vector = vector(data)
            self.n = int(log(len(data), 2))
        elif "dge" in dtype:
            raise ImplementError("Edge length representation not implemented yet, please wait...")
    
    
    
    def polytope_from_simplices_vector(self): # Wrong if negative coefficients
        self.polytope = sum(self.simplicies_vector[x] * Delta(X, self.n) for X in self.simplicies_vector
                            if self.simplicies_vector[x] != 0)
        return None
    
    def polytope_from_shards_vector(self): # Wrong if negative coefficients
        self.polytope = sum(self.shards_vector[x] * shard(alpha, self.n) for alpha in self.shards_vector
                            if self.shards_vector[x] != 0)
        return None
    
    def polytope_from_submodular_func(self):
        self.polytope = P_h(self.submodular_func, self.n)
        return None
    
    def shards_vector_from_simplicies_vector(self):
        self.shards_vector = {alpha : 0 for alpha in all_arcs(self.n)}
        threshold = self.n^3                      # Discuss that
        if self.is_sparse_simplicies_vector:
            c = 0
            self.shards_used = set()
            for J in self.simplicies_used:
                if self.simplicies_vector[J] != 0:
                    for I in all_worst_Subsets_for_shard(J):
                        alpha = arc_of_subset(I)
                        self.shards_vector[alpha] += (-1)^len({min(I), max(I)}.intersection({min(J), max(J)})) * self.simplicies_vector[J]
                        if c <= threshold:
                            self.shards_used.add(alpha)
                            c = len(self.shards_used)
            if len(self.shards_used) <= threshold:
                self.is_sparse_shards_vector = True
            else:
                self.shards_used = set()
        else:
            for J in self.simplicies_vector:
                if self.simplicies_vector[J] != 0:
                    for I in all_worst_Subsets_for_shard(J):
                        alpha = arc_of_subset(I)
                        self.shards_vector[alpha] += (-1)^len({min(I), max(I)}.intersection({min(J), max(J)})) * self.simplicies_vector[J]
        return None
    
    def simplicies_vector_from_shards_vector(self):
        self.simplicies_vector = {X : 0 for X in Susbsets(range(self.n)) if len(X) != 0}
        threshold = self.n^3                      # Discuss that
        if self.is_sparse_shards_vector:
            c = 0
            self.simplicies_used = set()
            for alpha in self.shards_used:
                if self.shard_vector[alpha] != 0:
                    I = Set({alpha[0], alpha[1]}).union(alpha[2])
                    for J in all_worst_Subsets_for_shard(I):
                        self.simplicies_vector[J] += (-1)^J_I(J, I) * self.shard_vector[I]
                        if c <= threshold:
                            self.simplicies_used.add(alpha)
                            c = len(self.simplicies_used)
            if len(self.simplices_used) <= threshold:
                self.is_sparse_simplices_vector = True
            else:
                self.simplices_used = set()
        else:
            for alpha in self.shard_vector:
                if self.shard_vector[alpha] != 0:
                    I = Set({alpha[0], alpha[1]}).union(alpha[2])
                    for J in all_worst_Subsets_for_shard(I):
                        self.simplicies_vector[J] += (-1)^J_I(J, I) * self.shard_vector[I]
        return None
    
    def submodular_func_from_polytope(self):
        self.submodular_func = submodular_func(self.P, self.n)
        return None
    
    def simplicies_vector_from_submodular_func(self):
        MSF = submodular_matrix_simplicies(self.n)
        submod_vec = vector([self.submodular_func[X] for X in Subsets(range(self.n))
                              if not len(X) in {0, self.n}])
        vs = MSF.solve_right(submod_vec)
        self.simplicies_vector = dict()
        c = 0
        for X in Subsets(range(self.n)):
            if not len(X) in {0, self.n}:
                self.simplicies_vector[X] = vs[c]
                c += 1
        return None
    
    def shards_vector_from_submodular_func(self):
        MSF = submodular_matrix_shards(self.n)
        submod_vec = vector([self.submodular_func[X] for X in Subsets(range(self.n))
                              if not len(X) in {0, self.n}])
        vs = MSF.solve_right(submod_vec)
        self.shards_vector = dict()
        c = 0
        for alpha in all_arcs(self.n):
            self.shards_vector[alpha] = vs[c]
            c += 1
        return None
    
    
    
    
    
    
    
    
    
def Delta(X, n):
    return Polyhedron(vertices = [[int(i == j) for i in range(n)] for j in X])

def all_alterning_matching(X, Y):
    G = DiGraph()
    for x in X:
        G.add_edges((x, y) for y in Y if x < y)
    for y in Y:
        G.add_edges((y, x) for x in X if x > y)
    G.add_edges(("start", x) for x in X)
    G.add_edges((y, "end") for y in Y)
    G.add_edge(("start", "end"))
    for path in G.all_paths_iterator(["start"], ["end"]):
        lp = len(path)
        yield [path[i] for i in range(1, lp-1, 2)], [path[j] for j in range(2, lp-1, 2)]

def shard_polytope(alpha, n):
    a, b, A, B = alpha
    return Polyhedron(vertices = [[int(i in am[0]) - int(i in am[1]) for i in range(n)]
                                  for am in all_alterning_matching([a]+list(alpha[2]), list(alpha[3])+[b])])

def g_vec(S, n):
    return [int(i in S) - len(S)/n for i in range(n)]

def P_h(h, n):
    Ieqs = []
    for X in Subsets(range(n)):
        if not len(X) in {0, n}:
            Ieqs.append([-h[X]] + g_vec(X, n))
    return Polyhedron(eqns = [[-h[Set(range(n))]] + [1]*n], ieqs = Ieqs)

def submodular_func(P, n):
    """Should be optimized"""
    fu = []
    for k in range(2^n):
        v = vector(g_vec(bin_to_set(k), n))
        fu.append(min(v.dot_product(u.vector()) for u in P.vertices()))
    return vector(fu)

def submodular_matrix_simplicies(n):
    """Should be made a constant of the class, but I don't
    know how to code that.
    Especially, if the user have several GP in the same
    ambient space, do not re-compute this matrix.
    + Optimize this computation!
    """
    DD = [Delta(X, n) - QQ(len(X)/n) * vector([1]*n) for X in Subsets(range(n)) if X != Set() and X != Set({n-1})]
    DDSF = [submodular_func(Q, n) for Q in DD]
    return Matrix(DDSF).T

def all_arcs(n = 5):
    """Iterator over all arcs on `n` points"""
    for a in range(n):
        for b in range(a+1, n):
            for S in Subsets(range(a+1, b)):
                yield (a, b, Set(S), Set(range(a+1, b)).difference(S))

def submodular_matrix_shards(n):
    """Should be made a constant of the class, but I don't
    know how to code that.
    Especially, if the user have several GP in the same
    ambient space, do not re-compute this matrix.
    + Optimize this computation!
    """
    SP = [shard_polytope(alpha, n) for alpha in all_arcs(n)]
    SPSF = [submodular_func(Q, n) for Q in DD]
    return Matrix(SPSF).T

def all_worst_Subsets_for_shard(I):
    for J in Subsets(set(range(min(I)+1, max(I))).symmetric_difference(set(I))):
        if len(J) >= 2:
            yield J.union(Set(I).intersection(Set(range(min(J)+1, max(J)))))
    return None

def J_I(J, I):
    return len(J.difference(Set({min(J), max(J)}).union(Set(I))))

def arc_of_subset(I):
    mI, MI = min(I), max(I)
    return (mI, MI, I.difference(Set({mI, MI})), Set(range(mI+1, MI)).difference(I))

def Delta_printer(w, no_translations = False):
    def print_set(X):
        return "D" + sum_str([str(x) for x in X])
    XX = [X for X in Subsets(range(n)) if X != Set() and X != Set({n-1})]
    s = ""
    if no_translations:
        st = n-1
    else:
        st = 0
    for k in range(st, len(w)):
        if w[k] == 1:
            s += "+ " + print_set(XX[k]) + " "
        elif w[k] == -1:
            s += "- " + print_set(XX[k]) + " "
        elif w[k] > 0:
            s += "+ " + str(w[k]) + "* " + print_set(XX[k]) + " "
        elif w[k] < 0:
            s += "- " + str(-w[k]) + "* " + print_set(XX[k]) + " "
    return s[2 : -1]

In [ ]:
def graphical_zonotope(G):
    n = G.num_verts()
    return sum(Polyhedron(vertices=[[int(i == e[0]) for i in range(n)], [int(i == e[1]) for i in range(n)]]) for e in G.edges())



def hypergraphic_polytope(HH, n = -1):
    """Also for nestohedron"""
    if n == -1:
        n = max(max(H) for H in HH)
    return sum(Delta(H, n) for H in HH)

def matroid_polytope(M, n = -1):
    """M given as a list of bases"""
    if n == -1:
        n = max(max(B) for B in M)
    return Polyhedron(vertices = [[int(i in B) for i in range(n)] for B in M])

def removahedron(SS, n = -1):
    """Be careful for the eqns you wish..."""
    if n == -1:
        n = max(max(S) for S in SS)
    Eq = [[-n*(n+1)/2] + [1]*n]
    Iq = [[-(len(S)+1)*len(S)/2] + [int(i in S) for i in range(n)] for S in SS]
#     print(Polyhedron(eqns=Eq, ieqs=Iq))
    return Polyhedron(eqns=Eq, ieqs=Iq)

In [18]:
def J_better_I(J, I):
        mI, MI = min(I), max(I)
        mJ, MJ = min(J), max(J)
        return {mJ, MJ}.issubset(set(range(mI+1, MI)).symmetric_difference(set(I))) and (set(range(mJ+1, MJ)).intersection(set(I))).issubset(set(J))

    def all_better(J, n = -1):
        if n == -1:
            n = max(J) + 1
        return None

In [17]:
I = {1, 3, 4}
for J in all_worst(I):
    print(J, J_I(J, I))

{1, 2} 0
{1, 3, 4} 0
{2, 3, 4} 0
{1, 2, 3, 4} 1


In [30]:
n = 4
M = Matrix([[J_I(J, I) for J in Subsets(range(n)) if len(J) >= 2] for I in Subsets(range(n))  if len(I) >= 2])
print(M)

[0 0 0 0 0 0 0 0 1 1 1]
[0 0 0 0 0 0 1 1 0 0 1]
[0 0 0 0 0 0 1 1 1 1 2]
[0 0 0 0 0 0 0 0 0 0 0]
[0 0 0 0 0 0 0 0 1 1 1]
[0 0 0 0 0 0 1 1 0 0 1]
[0 0 0 0 0 0 0 0 0 0 0]
[0 0 0 0 0 0 0 0 1 1 1]
[0 0 0 0 0 0 1 1 0 0 1]
[0 0 0 0 0 0 0 0 0 0 0]
[0 0 0 0 0 0 0 0 0 0 0]


In [ ]:
# Utilitaries :
# copy-paste what you want and then suppress this cell



def iota_vec(S, n):
    return [-1 + 2*int(i in S) for i in range(n)]

def e_S(S, n):
    return [int(i in S) for i in range(n)]



def is_generalized_permutahedron(P):
    for u, v, _ in P.graph().edges():
        w = u.vector() - v.vector()
        supp = [i for i in range(len(w)) if w[i] != 0]
        if len(supp) != 2 or w[supp[0]] != - w[supp[1]]:
            return False
    return True

def is_building_set(B):
    lB = len(B)
    Bcopy = [set(X) for X in B]
    for ind1 in range(lB):
        for ind2 in range(ind1+1, lB):
            X, Y = Bcopy[ind1], Bcopy[ind2]
            if len(X.intersection(Y)) > 0:
                if not X.union(Y)  in Bcopy:
                    return False
    return True

def all_arcs(n = 5):
    """Iterator over all arcs on `n` points"""
    for a in range(n):
        for b in range(a+1, n):
            for S in Subsets(range(a+1, b)):
                yield (a, b, set(S), set(range(a+1, b)).difference(S))

def arc_ideal_generated_by(Alpha):
    """Return the ideal (for dominance/restriction relation) generated by the list of arc `Alpha` (works also if `Alpha` is just an arc an not given as a list)"""
    if type(Alpha) == tuple:
        L = [Alpha]
    else:
        L = list(Alpha)
    n = max(alpha[1] for alpha in L)
    D = {(a, b) : [] for a in range(n+1) for b in range(a+1, n+1)}
    for a, b, S, U in L:
        for c in range(a, b+1):
            for d in range(c+1, b+1):
                beta = (c, d, S.intersection(set(range(c+1, d))), U.intersection(set(range(c+1, d))))
                if not beta in D[(c, d)]:
                    D[(c, d)].append(beta)
    L = []
    for l in D.values():
        L += l
    return L

def is_dominating_arc(alpha, beta):
    """Dominance/restriction relation between arcs (return whether `beta` is a restriction of `alpha` or not)"""
    return (alpha[0] <= beta[0]) and (beta[1] <= alpha[1]) and (alpha[2].intersection(set(range(beta[0]+1, beta[1]))) == beta[2])

def arc_dominance_poset(n):
    """Return the poset obtained from the dominance/restriction relation"""
    return Poset(([(a, b, frozenset(S), frozenset(U)) for (a, b, S, U) in all_arcs(n)], lambda alpha, beta : is_dominating_arc(beta, alpha)))

def arc_ideals_poset(n):
    """Return the lattice of (downward) ideals (or down sets) of the dominance poset"""
    arc_Po = arc_dominance_poset(n)
    return arc_Po.order_ideals_lattice()



def quotientope(Alpha, n):
    return sum(shard_polytope(alpha, n) for alpha in Alpha)

def cut_function(G):
    n = G.num_verts()
    L = []
    for k in range(2^n):
        X = bin_to_set(k)
        L.append(sum( (e[0] in X and not e[1] in X) or (e[1] in X and not e[0] in X) for e in G.edges()))
    return tuple(L)

def cut_polytope(G):
    return P_h(-vector(cut_function(G)))